In [0]:
import requests
import pandas as pd
import math

import json
from functools import reduce

# Matplotlib for visualization at the end
import matplotlib.pyplot as plt
import seaborn as sns

from pyspark.sql.functions import col, when, sum, when,lit, udf

from pyspark.sql.types import StructType, StructField, StringType, DoubleType

from pyspark.ml.feature import VectorAssembler, StandardScaler
from pyspark.ml.clustering import KMeans
from pyspark.ml.evaluation import ClusteringEvaluator

## Grouping the features

In [0]:
# Features

wind = ["wind_speed_10m", "wind_speed_120m","wind_direction_10m", "wind_direction_120m","wind_gusts_10m"]

cloud_cover = ["cloud_cover", "cloud_cover_low", "cloud_cover_mid", "cloud_cover_high", "visibility"]

# realtive_humidity_2m: is the ratio of the actual water vapor in the air to the maximum the air can hold at that temperature (in %)
# dew_point_2m: temperature at which air becomes saturated with moisture
# vapour_pressure_deficit: difference between the amount of moisture in the air and how much it can hold when saturated.
temperature = ["apparent_temperature", "temperature_2m", "temperature_120m","relative_humidity_2m", "dew_point_2m", "vapour_pressure_deficit"]

rain_snow = ["precipitation_probability", "precipitation", "rain", "showers", "snowfall", "snow_depth"]

pressure = ["surface_pressure", "pressure_msl"]

water_balance = ["evapotranspiration", "et0_fao_evapotranspiration"]


## Loading the data

In [0]:
url = "https://historical-forecast-api.open-meteo.com/v1/forecast"

dfs={}

# create pandas dataframes with the different types of features
# after transform the pandas data frane into a spark data frame

features = {
    'wind': wind, 
    'cloud_cover': cloud_cover, 
    'temperature': temperature, 
    'rain_snow': rain_snow,
    'pressure': pressure, 
    'water_balance': water_balance
    }

for key, value in features.items():
	params = {
		# Lisbon coordinates
		"latitude": 38.716885,
		"longitude": -9.140233,
		# 1 Year Historical data
		"start_date": "2023-05-01",
		"end_date": "2025-05-01",
		"hourly": value
	}

	response = requests.get(url, params=params)
	data = response.json()
	pdf = pd.DataFrame(data['hourly'])
	dfs[key] = spark.createDataFrame(pdf)

In [0]:
# columns on the wind df as an example
dfs['wind'].columns


Out[4]: ['time',
 'wind_speed_10m',
 'wind_speed_120m',
 'wind_direction_10m',
 'wind_direction_120m',
 'wind_gusts_10m']

In [0]:
# list of dataframes extracted from the dictionary
dfs_list = list(dfs.values())

# merge all DataFrames on the 'time' column with an outer join, reduce is used to simplify code
# so that we dont have to do all the joins one by one
df_merged = reduce(lambda left, right: left.join(right, on="time", how="outer"), dfs_list)


## Check for missing values

In [0]:
for group_feat in dfs.keys(): # check missing values
    dfs[group_feat].select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in dfs[group_feat].columns]).show()


+----+--------------+---------------+------------------+-------------------+--------------+
|time|wind_speed_10m|wind_speed_120m|wind_direction_10m|wind_direction_120m|wind_gusts_10m|
+----+--------------+---------------+------------------+-------------------+--------------+
|   0|             0|              0|                 0|                  0|             0|
+----+--------------+---------------+------------------+-------------------+--------------+

+----+-----------+---------------+---------------+----------------+----------+
|time|cloud_cover|cloud_cover_low|cloud_cover_mid|cloud_cover_high|visibility|
+----+-----------+---------------+---------------+----------------+----------+
|   0|          0|              0|              0|               0|         0|
+----+-----------+---------------+---------------+----------------+----------+

+----+--------------------+--------------+----------------+--------------------+------------+-----------------------+
|time|apparent_temperatur

In [0]:
df_merged.columns

Out[33]: ['time',
 'wind_speed_10m',
 'wind_speed_120m',
 'wind_direction_10m',
 'wind_direction_120m',
 'wind_gusts_10m',
 'cloud_cover',
 'cloud_cover_low',
 'cloud_cover_mid',
 'cloud_cover_high',
 'visibility',
 'apparent_temperature',
 'temperature_2m',
 'temperature_120m',
 'relative_humidity_2m',
 'dew_point_2m',
 'vapour_pressure_deficit',
 'precipitation_probability',
 'precipitation',
 'rain',
 'showers',
 'snowfall',
 'snow_depth',
 'surface_pressure',
 'pressure_msl',
 'evapotranspiration',
 'et0_fao_evapotranspiration']

In [0]:
df_merged=df_merged.drop('precipitation_probability') # drop the only column with missing values (ot only has missing values)

## Use SQL to do queries

In [0]:
# regist the dataframe in a view to query with sql
df_merged.createOrReplaceTempView("df_merged")

In [0]:
%sql
SELECT *
FROM df_merged

time wind_speed_10m wind_speed_120m wind_direction_10m wind_direction_120m wind_gusts_10m cloud_cover cloud_cover_low cloud_cover_mid cloud_cover_high visibility apparent_temperature temperature_2m temperature_120m relative_humidity_2m dew_point_2m vapour_pressure_deficit precipitation rain showers snowfall snow_depth surface_pressure pressure_msl evapotranspiration et0_fao_evapotranspiration 2023-05-01T00:00 6.2 21.4 21 7 18.0 0 0 0 0 24140.0 16.3 16.6 16.2 73 11.8 0.51 0.0 0.0 0.0 0.0 0.0 1014.5 1018.3 0.01 0.01 2023-05-01T01:00 4.5 19.8 14 2 13.0 0 0 0 0 24140.0 16.3 16.5 16.4 73 11.6 0.51 0.0 0.0 0.0 0.0 0.0 1014.2 1018.0 0.01 0.0 2023-05-01T02:00 3.0 18.8 346 355 10.4 0 0 0 0 24140.0 16.1 16.3 16.7 69 10.6 0.58 0.0 0.0 0.0 0.0 0.0 1013.7 1017.5 0.01 0.0 2023-05-01T03:00 3.2 18.8 360 357 6.8 100 0 0 100 24140.0 15.7 16.1 16.7 67 10.0 0.61 0.0 0.0 0.0 0.0 0.0 1013.7 1017.5 0.01 0.0 2023-05-01T04:00 3.0 17.7 346 355 5.8 42 0 0 42 24140.0 15.6 16.1 16.7 66 9.7 0.62 0.0 0.0 0.0 0.0 0.0 1014.0 1017.8 0.01 0.0 2023-05-01T05:00 3.6 19.4 6 360 8.3 96 0 0 96 24140.0 15.4 16.0 16.6 66 9.7 0.62 0.0 0.0 0.0 0.0 0.0 1014.0 1017.8 0.01 0.0 2023-05-01T06:00 3.4 16.7 32 6 9.0 29 0 0 29 24140.0 15.3 15.8 16.6 68 9.9 0.58 0.0 0.0 0.0 0.0 0.0 1013.9 1017.7 0.01 0.03 2023-05-01T07:00 3.3 14.5 41 14 7.2 0 0 0 0 24140.0 16.4 16.6 16.6 70 11.1 0.57 0.0 0.0 0.0 0.0 0.0 1014.0 1017.8 0.01 0.05 2023-05-01T08:00 5.0 11.7 21 18 14.4 0 0 0 0 24140.0 18.5 19.0 16.9 59 10.8 0.9 0.0 0.0 0.0 0.0 0.0 1014.4 1018.2 0.04 0.17 2023-05-01T09:00 7.0 9.2 21 21 19.4 0 0 0 0 24140.0 20.7 21.5 18.7 50 10.6 1.28 0.0 0.0 0.0 0.0 0.0 1014.5 1018.3 0.09 0.32 2023-05-01T10:00 9.2 12.4 26 26 24.5 0 0 0 0 24140.0 23.5 23.6 20.4 46 11.3 1.57 0.0 0.0 0.0 0.0 0.0 1014.3 1018.0 0.13 0.46 2023-05-01T11:00 9.3 12.7 28 25 25.6 0 0 0 0 24140.0 26.5 25.5 22.0 43 12.0 1.86 0.0 0.0 0.0 0.0 0.0 1014.2 1017.9 0.16 0.57 2023-05-01T12:00 7.7 9.7 28 27 25.2 3 0 0 3 24140.0 28.9 26.9 23.1 41 12.6 2.1 0.0 0.0 0.0 0.0 0.0 1013.7 1017.4 0.19 0.65 2023-05-01T13:00 6.2 6.6 353 351 14.0 7 0 0 7 24140.0 29.6 28.3 24.5 29 8.6 2.74 0.0 0.0 0.0 0.0 0.0 1013.4 1017.1 0.2 0.69 2023-05-01T14:00 8.0 9.0 280 275 20.2 0 0 0 0 24140.0 29.4 28.8 25.0 27 7.9 2.89 0.0 0.0 0.0 0.0 0.0 1012.9 1016.6 0.19 0.69 2023-05-01T15:00 13.7 19.1 267 266 32.8 0 0 0 0 24140.0 29.1 28.4 24.6 40 13.5 2.32 0.0 0.0 0.0 0.0 0.0 1013.2 1016.9 0.17 0.63 2023-05-01T16:00 14.3 22.1 311 314 35.6 0 0 0 0 24140.0 27.3 27.9 24.4 37 11.9 2.37 0.0 0.0 0.0 0.0 0.0 1013.1 1016.8 0.13 0.54 2023-05-01T17:00 14.8 23.7 331 332 36.7 8 0 0 8 24140.0 24.3 26.5 23.5 35 9.8 2.25 0.0 0.0 0.0 0.0 0.0 1012.8 1016.5 0.11 0.43 2023-05-01T18:00 13.1 21.8 339 338 35.6 2 0 0 2 24140.0 23.3 25.2 22.8 38 9.9 1.99 0.0 0.0 0.0 0.0 0.0 1012.2 1015.9 0.09 0.28 2023-05-01T19:00 11.3 21.1 353 351 32.0 100 0 0 100 24140.0 21.1 23.0 21.3 41 9.1 1.66 0.0 0.0 0.0 0.0 0.0 1012.1 1015.8 0.05 0.15 2023-05-01T20:00 7.3 20.9 11 4 26.6 86 0 0 86 24140.0 20.3 21.6 20.7 45 9.2 1.42 0.0 0.0 0.0 0.0 0.0 1012.8 1016.6 0.03 0.08 2023-05-01T21:00 4.7 17.7 32 12 16.6 20 0 0 20 24140.0 19.6 20.4 20.0 50 9.6 1.2 0.0 0.0 0.0 0.0 0.0 1012.9 1016.7 0.03 0.03 2023-05-01T22:00 3.7 16.7 29 7 10.1 35 0 0 35 24140.0 19.0 19.4 19.8 56 10.4 0.99 0.0 0.0 0.0 0.0 0.0 1013.2 1017.0 0.02 0.01 2023-05-01T23:00 3.3 16.5 41 11 7.2 93 0 0 93 24140.0 18.4 18.8 19.8 57 10.1 0.94 0.0 0.0 0.0 0.0 0.0 1013.1 1016.9 0.01 0.01 2023-05-02T00:00 4.3 18.0 66 26 6.5 100 0 0 100 24140.0 17.5 18.1 19.4 59 10.0 0.85 0.0 0.0 0.0 0.0 0.0 1012.6 1016.4 0.01 0.01 2023-05-02T01:00 4.0 17.2 85 37 9.4 100 0 0 100 24140.0 17.1 17.5 19.2 64 10.6 0.72 0.0 0.0 0.0 0.0 0.0 1012.1 1015.9 0.01 0.01 2023-05-02T02:00 4.7 19.1 90 44 10.1 100 0 0 100 24140.0 16.3 16.8 18.8 66 10.4 0.65 0.0 0.0 0.0 0.0 0.0 1011.5 1015.3 0.01 0.01 2023-05-02T03:00 4.8 21.4 77 45 9.7 100 0 0 100 24140.0 15.8 16.5 18.3 66 10.1 0.64 0.0 0.0 0.0 0.0 0.0 1011.3 1015.1 0.01 0.01 2023-05-02T04:00 4.1 20.6 75 47 9.4 89 0 0 89 24140.0 15.7 16.2 18.3 67 10.1 0

In [0]:
%sql
-- see the correlations
SELECT 
corr(wind_speed_10m,
 wind_direction_10m) AS correlation_speed10_direction10,
corr(wind_speed_10m, wind_speed_120m) AS correlation_speed10_speed120,
corr(wind_direction_10m, wind_direction_120m) AS correlation_direction10_direction120,
corr(wind_speed_10m, wind_gusts_10m) AS correlation_speed10_gusts10,
corr(wind_direction_10m, wind_gusts_10m) AS correlation_direction10_gusts10
FROM df_merged;

correlation_speed10_direction10 correlation_speed10_speed120 correlation_direction10_direction120 correlation_speed10_gusts10 correlation_direction10_gusts10 0.22535395172605127 0.8335900366635401 0.8971379164623488 0.9654900879984376 0.2838115525230414

## Trying to split into months years and hours

In [0]:
from pyspark.sql.functions import to_timestamp

df_merged = df_merged.withColumn("time_ts", to_timestamp("time", "yyyy-MM-dd'T'HH:mm"))


In [0]:
from pyspark.sql.functions import year, month, hour

df_merged = df_merged.withColumn("year", year("time_ts")) \
       .withColumn("month", month("time_ts")) \
       .withColumn("hour", hour("time_ts"))


In [0]:
df_merged.columns

Out[52]: ['time',
 'wind_speed_10m',
 'wind_speed_120m',
 'wind_direction_10m',
 'wind_direction_120m',
 'wind_gusts_10m',
 'cloud_cover',
 'cloud_cover_low',
 'cloud_cover_mid',
 'cloud_cover_high',
 'visibility',
 'apparent_temperature',
 'temperature_2m',
 'temperature_120m',
 'relative_humidity_2m',
 'dew_point_2m',
 'vapour_pressure_deficit',
 'precipitation',
 'rain',
 'showers',
 'snowfall',
 'snow_depth',
 'surface_pressure',
 'pressure_msl',
 'evapotranspiration',
 'et0_fao_evapotranspiration',
 'time_ts',
 'year',
 'month',
 'hour']

In [0]:
df_merged.groupBy("year", "month", "hour").count().show()


+----+-----+----+-----+
|year|month|hour|count|
+----+-----+----+-----+
|2023|    5|  18|   31|
|2024|    3|  19|   31|
|2025|    3|  19|   31|
|2024|    2|  10|   29|
|2025|    3|   9|   31|
|2024|    1|  13|   31|
|2024|   11|  13|   30|
|2025|    2|  19|   28|
|2024|   11|  20|   30|
|2023|    9|   4|   30|
|2023|    8|  10|   31|
|2025|    2|  12|   28|
|2025|    5|   5|    1|
|2024|    3|  15|   31|
|2023|   12|   9|   31|
|2024|    7|   0|   31|
|2024|   11|   1|   30|
|2025|    3|  10|   31|
|2023|    7|   4|   31|
|2025|    1|   7|   31|
+----+-----+----+-----+
only showing top 20 rows

